### Ici nous allons proceder a l'optimisation des hyperparametres de nos 3 modeles d'apprentissage : XGBoost, LightGBM et CatBoost en utilisant la validation croisee d'ordre k et la tree structured parzen estimator 

In [87]:
# Importation des librairies nécessaires
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import seaborn as sns
import numpy as np
from sklearn.model_selection import KFold, cross_val_score, train_test_split

In [88]:
#creation d'un dataframe panda
df=pd.read_excel("Concrete_Data.xls")
df.head(20)

Cement (component 1)(kg in a m^3 mixture)  \
0                                       540.0   
1                                       540.0   
2                                       332.5   
3                                       332.5   
4                                       198.6   
5                                       266.0   
6                                       380.0   
7                                       380.0   
8                                       266.0   
9                                       475.0   
10                                      198.6   
11                                      198.6   
12                                      427.5   
13                                      190.0   
14                                      304.0   
15                                      380.0   
16                                      139.6   
17                                      342.0   
18                                      380.0   
19                                      475.0   

    Blast Furnace Slag (component 2)(kg in a m^3 mixture)  \
0                                                 0.0       
1                                                 0.0       
2                                               142.5       
3                                               142.5       
4                                               132.4       
5                                               114.0       
6                                                95.0       
7                                                95.0       
8                                               114.0       
9                                                 0.0       
10                                              132.4       
11                                              132.4       
12                                               47.5       
13                                              190.0       
14                                               76.0       
15                                                0.0       
16                                              209.4       
17                                               38.0       
18                                               95.0       
19                                                0.0       

    Fly Ash (component 3)(kg in a m^3 mixture)  \
0                                          0.0   
1                                          0.0   
2                                          0.0   
3                                          0.0   
4                                          0.0   
5                                          0.0   
6                                          0.0   
7                                          0.0   
8                                          0.0   
9                                          0.0   
10                                         0.0   
11                                         0.0   
12                                         0.0   
13                                         0.0   
14                                         0.0   
15                                         0.0   
16                                         0.0   
17                                         0.0   
18                                         0.0   
19                                         0.0   

    Water  (component 4)(kg in a m^3 mixture)  \
0                                       162.0   
1                                       162.0   
2                                       228.0   
3                                       228.0   
4                                       192.0   
5                                       228.0   
6                                       228.0   
7                                       228.0   
8                                       228.0   
9                                       228.0   
10                                      192.0   
11                                      192.0   
12  

In [89]:
# Normalisation z-score ou standardisation
from sklearn.preprocessing import StandardScaler
scaler= StandardScaler()

normData=scaler.fit_transform(df)

normData

array([[ 2.47791782, -0.85688631, -0.84713204, ..., -1.21765845,
        -0.27973311,  2.64519215],
       [ 2.47791782, -0.85688631, -0.84713204, ..., -1.21765845,
        -0.27973311,  1.5612771 ],
       [ 0.49144303,  0.79553263, -0.84713204, ..., -2.24091255,
         3.55306569,  0.26660766],
       ...,
       [-1.2700575 ,  0.75958527,  0.85066095, ...,  0.08012724,
        -0.27973311, -0.7259282 ],
       [-1.16857975,  1.3080724 , -0.84713204, ...,  0.19118775,
        -0.27973311, -0.18264932],
       [-0.19401043,  0.30850389,  0.37696733, ..., -0.15072887,
        -0.27973311, -0.20461667]])

In [90]:
# Convertir le tableau obtenu en un dataframe
normData=pd.DataFrame(normData)
normData

0         1         2         3         4         5         6  \
0     2.477918 -0.856886 -0.847132 -0.916663 -0.620225  0.863160 -1.217658   
1     2.477918 -0.856886 -0.847132 -0.916663 -0.620225  1.056170 -1.217658   
2     0.491443  0.795533 -0.847132  2.175367 -1.038944 -0.526514 -2.240913   
3     0.491443  0.795533 -0.847132  2.175367 -1.038944 -0.526514 -2.240913   
4    -0.790432  0.678414 -0.847132  0.488805 -1.038944  0.070531  0.647908   
...        ...       ...       ...       ...       ...       ...       ...   
1025 -0.045623  0.488241  0.564569 -0.092122  0.451695 -1.323003 -0.065874   
1026  0.392837 -0.856886  0.960095  0.676201  0.702927 -1.994679  0.496916   
1027 -1.270057  0.759585  0.850661  0.521599 -0.017270 -1.036061  0.080127   
1028 -1.168580  1.308072 -0.847132 -0.279518  0.853666  0.214646  0.191188   
1029 -0.194010  0.308504  0.376967  0.891706  0.401449 -1.395060 -0.150729   

             7         8  
0    -0.279733  2.645192  
1    -0.279733  1.561277  
2     3.553066  0.266608  
3     5.057677  0.313515  
4     4.978487  0.507753  
...        ...       ...  
1025 -0.279733  0.507051  
1026 -0.279733 -0.277827  
1027 -0.279733 -0.725928  
1028 -0.279733 -0.182649  
1029 -0.279733 -0.204617  

[1030 rows x 9 columns]

In [91]:
req_col_names = ["Cement", "BlastFurnaceSlag", "FlyAsh", "Water", "Superplasticizer",
                 "CoarseAggregate", "FineAggregate", "Age", "CC_Strength"]
curr_col_names = list(normData.columns)

mapper = {}
for i, name in enumerate(curr_col_names):
    mapper[name] = req_col_names[i]

normData = normData.rename(columns=mapper)

normData.head()

Cement  BlastFurnaceSlag    FlyAsh     Water  Superplasticizer  \
0  2.477918         -0.856886 -0.847132 -0.916663         -0.620225   
1  2.477918         -0.856886 -0.847132 -0.916663         -0.620225   
2  0.491443          0.795533 -0.847132  2.175367         -1.038944   
3  0.491443          0.795533 -0.847132  2.175367         -1.038944   
4 -0.790432          0.678414 -0.847132  0.488805         -1.038944   

   CoarseAggregate  FineAggregate       Age  CC_Strength  
0         0.863160      -1.217658 -0.279733     2.645192  
1         1.056170      -1.217658 -0.279733     1.561277  
2        -0.526514      -2.240913  3.553066     0.266608  
3        -0.526514      -2.240913  5.057677     0.313515  
4         0.070531       0.647908  4.978487     0.507753

In [92]:
normData.describe()

Cement  BlastFurnaceSlag        FlyAsh         Water  \
count  1.030000e+03       1030.000000  1.030000e+03  1.030000e+03   
mean   9.657862e-17          0.000000  2.759389e-17  3.587206e-16   
std    1.000486e+00          1.000486  1.000486e+00  1.000486e+00   
min   -1.715219e+00         -0.856886 -8.471320e-01 -2.802333e+00   
25%   -8.500258e-01         -0.856886 -8.471320e-01 -7.808013e-01   
50%   -7.912996e-02         -0.601776 -8.471320e-01  1.608624e-01   
75%    6.589771e-01          0.800751  1.001836e+00  4.888051e-01   
max    2.477918e+00          3.310688  2.281122e+00  3.065497e+00   

       Superplasticizer  CoarseAggregate  FineAggregate           Age  \
count      1.030000e+03     1.030000e+03   1.030000e+03  1.030000e+03   
mean      -2.759389e-17     2.276496e-16  -1.931572e-16  2.069542e-17   
std        1.000486e+00     1.000486e+00   1.000486e+00  1.000486e+00   
min       -1.038944e+00    -2.212137e+00  -2.240913e+00 -7.073594e-01   
25%       -1.038944e+00    -5.265140e-01  -5.319534e-01 -6.123314e-01   
50%        2.460198e-02    -6.328926e-02   7.401267e-02 -2.797331e-01   
75%        6.627297e-01     7.267662e-01   6.291904e-01  1.637312e-01   
max        4.354156e+00     2.214232e+00   2.733101e+00  5.057677e+00   

        CC_Strength  
count  1.030000e+03  
mean   2.759389e-16  
std    1.000486e+00  
min   -2.005443e+00  
25%   -7.252985e-01  
50%   -8.235105e-02  
75%    6.179613e-01  
max    2.801689e+00

In [93]:
X = normData.iloc[:,:-1]
y = normData.iloc[:,-1]

In [94]:
# 
# kft=KFold(n_splits=10,shuffle=True,random_state=42)

# cnt = 1
# # split()  method generate indices to split data into training and test set.
# for train_index, test_index in kft.split(X, y):
#     print(f'Fold:{cnt}, Train set: {len(train_index)}, Test set:{len(test_index)}')
#     cnt += 1

In [95]:
# import xgboost as xgb
# from xgboost import XGBRegressor

# xgbr = XGBRegressor()

# score = cross_val_score(xgbr, X, y, cv= kft, scoring="neg_mean_squared_error")

In [96]:
# score

In [97]:
# def rmse(score):
#     rmse = np.sqrt(-score)
#     # print(f'rmse= {"{:.3f}".format(rmse)}')
#     return rmse

In [98]:
#rmse(score.mean())

In [99]:
# import lightgbm as lgbm
# from lightgbm import LGBMRegressor
# lgb=LGBMRegressor()

# score2 = cross_val_score(lgb,X,y,cv=kft,scoring="neg_mean_squared_error")
# score2

In [100]:
# rmse(score2.mean())

#### XGBoost

In [101]:
# Defining hyperparameter search space for the three models
from hyperopt import hp

search_space_xgb={
    "alpha":hp.uniform("alpha",0.05,1), #L1 regularization term on weigths
    "lambda":hp.uniform("lambda",0.05,1), #L2 regularization term on weigths 
    "eta":hp.uniform("eta",0.01,0.3),# learning rate
    "max_depth":hp.randint("max_depth",2,30),
    "subsample":hp.uniform("subsample",0.5,1),
    "max_bin":hp.randint("max_bin",10,2000),# maximum number of descrete bins  to bucket continuous features
    "gamma":hp.uniform("gamma",0,1), # min spleat loss
    "min_child_weight":hp.uniform("min_child_weight",0.1,10)# minimum sum of hessian(instance weigth) needed in a child
    # "colsample_by*":hp.uniform("colsample_by*",0.5,1)# subsample ratio of features
}

In [102]:
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=0.1,random_state=42)

In [103]:
# Defining the objective function
from sklearn.metrics import mean_squared_error, mean_absolute_error,r2_score
import xgboost
from xgboost import XGBRegressor

def objective_xgb(args):
    """This method is used to train the model xgboost using k-fold cross validation with k=10 as in the base article"""

    kf=KFold(n_splits=10,shuffle=True,random_state=42)
    rmse_tab_error = []
    mse_tab_error = []
    mae_tab_error = []
    r2_tab_error = []

    for train_index, test_index in kf.split(X_train):
        subX_train, subX_test = X_train.iloc[train_index], X_train.iloc[test_index]# sous echantillonnage du jeu d'entrainement
        suby_train, suby_test = y_train.iloc[train_index], y_train.iloc[test_index]# sous echantillonnage du jeu de test
        
        xgb = XGBRegressor(**args,random_state=42)

        xgb.fit(subX_train, suby_train)
    # score_x = cross_val_score(xgb, X_train, y_train, cv= kf, scoring="neg_mean_squared_error")

        y_pred = xgb.predict(subX_test)# predict for the sub test sample

        # predict in the last fold the model trained in the 9 folds 
        rmse = mean_squared_error(suby_test,y_pred,squared=False)
        mse = mean_squared_error(suby_test,y_pred)
        mae = mean_absolute_error(suby_test,y_pred)
        r2 = r2_score(suby_test, y_pred)

        ## append each metric for each fold in its corresponding table
        rmse_tab_error.append(rmse)
        mse_tab_error.append(mse)
        mae_tab_error.append(mae)
        r2_tab_error.append(r2)

    print("\n\n Hyperparameters : {}".format(args)) ## This can be commented if not needed.
    
    print("\n*********Test metrics*********\n")
    print("\t RMSE : {:.3f} \t MSE : {:.3f} \t MAE : {:.3f} \t R2 : {:.3f}".format(np.mean(np.array(rmse_tab_error)),
                        np.mean(np.array(mse_tab_error)), np.mean(np.array(mae_tab_error)), np.mean(np.array(r2_tab_error))))
   
    return np.mean(np.array(rmse_tab_error))

In [104]:
import hyperopt
trials_xgb=hyperopt.Trials()# It'll record different values of hyperparameters tried,
#objective function values during each trial, time of trials, state of the trial (success/failure), etc

results_xgb = hyperopt.fmin(objective_xgb,space=search_space_xgb,
                            algo=hyperopt.tpe.suggest,trials=trials_xgb,max_evals = 50)

#trials_xgb
# best_xgb_trial = trials_xgb.best_trial

                                                      

 Hyperparameters : {'alpha': 0.10945287293838567, 'eta': 0.08201017291698912, 'gamma': 0.33360093559682047, 'lambda': 0.6097463738106743, 'max_bin': 426, 'max_depth': 2, 'min_child_weight': 6.849711978876017, 'subsample': 0.6355904484042919}
                                                      
*********Test metrics*********

	 RMSE : 0.357 	 MSE : 0.130 	 MAE : 0.273 	 R2 : 0.869
                                                                               

 Hyperparameters : {'alpha': 0.48157512528219676, 'eta': 0.213931769596816, 'gamma': 0.8451544577731728, 'lambda': 0.8972619389341969, 'max_bin': 904, 'max_depth': 23, 'min_child_weight': 0.6416040392968699, 'subsample': 0.8167323925360472}
                                                                               
*********Test metrics*********

	 RMSE : 0.320 	 MSE : 0.104 	 MAE : 0.238 	 R2 : 0.895                        
                                             

In [105]:

results_xgb # best params to obtain the minimum loss which is the mean loss of all the trials


{'alpha': 0.5694646683442045,
 'eta': 0.10377410755425344,
 'gamma': 0.012156371236443909,
 'lambda': 0.7623161343760876,
 'max_bin': 1085,
 'max_depth': 9,
 'min_child_weight': 1.838072388064027,
 'subsample': 0.9117298454913538}

In [106]:
# trials_xgb.trials[5]['result']
Results_xgb= trials_xgb.results
Results_xgb[:5]# first five losses

[{'loss': 0.357171804476926, 'status': 'ok'},
 {'loss': 0.3199201941370317, 'status': 'ok'},
 {'loss': 0.3649935734261758, 'status': 'ok'},
 {'loss': 0.2910645371049378, 'status': 'ok'},
 {'loss': 0.32075819651450593, 'status': 'ok'}]

In [107]:
trials_xgb.average_best_error()# average of all differents losses of differents trials

0.2629461775814252

#### LightGBM

In [108]:
import lightgbm 
from lightgbm import LGBMRegressor
lgbm= LGBMRegressor()

In [109]:
import hyperopt
from hyperopt import hp
    
search_space_lgbm={
    "lambda_l1":hp.uniform("lambda_l1",0.05,7), #L1 regularization term on weigths
    "lambda_l2":hp.uniform("lambda_l2",0.05,7), #L2 regularization term on weigths 
    "learning_rate":hp.uniform("learning_rate",0.01,0.15),# learning rate
    "max_depth":hp.randint("max_depth",5,70),
    "subsample":hp.uniform("subsample",0.5,1),
    "max_bin":hp.randint("max_bin",50,2000),# maximum number of descrete bins  to bucket continuous features
    "min_gain_to_split":hp.uniform("min_gain_to_split",0,1), # min spleat loss
    "min_data_in_leaf" : hp.randint("min_data_in_leaf",2,31),# minimal number of data in one leaf
    "min_sum_hessian_in_leaf":hp.uniform("min_sum_hessian_in_leaf",0.1,10),# minimum sum of hessian(instance weigth) needed in a child
    "num_leaves":hp.randint("num_leaves",3,100)# subsample ratio of features
}

In [110]:
# Defining the objective function
def objective_lgbm(args):
    """This method is used to train the model lightgbm using k-fold cross validation with k=10 as in the base article"""

    kf=KFold(n_splits=10,shuffle=True,random_state=42)
    rmse_tab_error = []
    mse_tab_error = []
    mae_tab_error = []
    r2_tab_error = []

    for train_index, test_index in kf.split(X_train):
        subX_train, subX_test = X_train.iloc[train_index], X_train.iloc[test_index]# sous echantillonnage du jeu d'entrainement
        suby_train, suby_test = y_train.iloc[train_index], y_train.iloc[test_index]# sous echantillonnage du jeu de test
        
        lgbm = LGBMRegressor(**args,random_state=42)

        lgbm.fit(subX_train, suby_train)
    # score_x = cross_val_score(xgb, X_train, y_train, cv= kf, scoring="neg_mean_squared_error")

        y_pred = lgbm.predict(subX_test)# predict for the sub test sample

        # predict in the last fold the model trained in the 9 folds 
        rmse = mean_squared_error(suby_test,y_pred,squared=False)
        mse = mean_squared_error(suby_test,y_pred)
        mae = mean_absolute_error(suby_test,y_pred)
        r2 = r2_score(suby_test, y_pred)

        ## append each metric for each fold in its corresponding table
        rmse_tab_error.append(rmse)
        mse_tab_error.append(mse)
        mae_tab_error.append(mae)
        r2_tab_error.append(r2)

    print("\n\n Hyperparameters : {}".format(args)) ## This can be commented if not needed.
    
    print("\n*********Test metrics*********\n")
    print("\t RMSE : {:.3f} \t MSE : {:.3f} \t MAE : {:.3f} \t R2 : {:.3f}".format(np.mean(np.array(rmse_tab_error)),
                        np.mean(np.array(mse_tab_error)), np.mean(np.array(mae_tab_error)), np.mean(np.array(r2_tab_error))))
   
    return np.mean(np.array(rmse_tab_error))

In [111]:
from hyperopt import hp
trials_lgbm=hyperopt.Trials()# It'll record different values of hyperparameters tried,
#objective function values during each trial, time of trials, state of the trial (success/failure), etc

results_lgbm = hyperopt.fmin(objective_lgbm,space=search_space_lgbm,
                            algo=hyperopt.tpe.suggest,trials=trials_lgbm,max_evals = 50)

[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=7.203108646640537, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=7.203108646640537
[LightGBM] [Warning] min_gain_to_split is set=0.9997475480812857, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.9997475480812857
[LightGBM] [Warning] lambda_l2 is set=1.0542350613523164, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1.0542350613523164
[LightGBM] [Warning] lambda_l1 is set=3.342753931741053, reg_alpha=0.0 will be ignored. Current value: lambda_l1=3.342753931741053
[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=7.203108646640537, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=7.203108646640537
[

In [ ]:
results_lgbm

{'lambda_l1': 1.1418402509764554,
 'lambda_l2': 1.3464753350827496,
 'learning_rate': 0.13327629027436685,
 'max_bin': 627,
 'max_depth': 13,
 'min_data_in_leaf': 13,
 'min_gain_to_split': 0.3027899020982997,
 'min_sum_hessian_in_leaf': 9.54199775170039,
 'num_leaves': 77,
 'subsample': 0.8942812899235822}

In [ ]:
trials_lgbm.average_best_error()

0.3274933919950479

#### CatBoost

In [ ]:
import catboost
from catboost import CatBoostRegressor


search_space_catb={
   "l2_leaf_reg":hp.uniform("l2_leaf_reg",0.05,20), #L2 regularization term on weigths
    "random_strength":hp.uniform("random_strength",0,100), #L2 regularization term on weigths 
    "learning_rate":hp.uniform("learning_rate",0.01,0.3),# learning rate
    # "depth":hp.randint("depth",2,30),
    "subsample":hp.uniform("subsample",0.5,1),
    "max_bin":hp.randint("max_bin",10,2000),# maximum number of descrete bins  to bucket continuous features
    "bagging_temperature":hp.uniform("bagging_temperature",0,100), # min spleat loss
    "min_data_in_leaf" : hp.randint("min_data_in_leaf",2,50),# minimal number of data in one leaf
    # "grow_policy":hp.choice("grow_policy",['Depthwise','Lossguide']),# minimum sum of hessian(instance weigth) needed in a child
    # "num_leaves":hp.randint("num_leaves",3,100)# subsample ratio of features
}

In [ ]:
def objective_catb(args):
    """This method is used to train the model catboost using k-fold cross validation with k=10 as in the base article"""

    kf=KFold(n_splits=10,shuffle=True,random_state=42)
    rmse_tab_error = []
    mse_tab_error = []
    mae_tab_error = []
    r2_tab_error = []

    for train_index, test_index in kf.split(X_train):
        subX_train, subX_test = X_train.iloc[train_index], X_train.iloc[test_index]# sous echantillonnage du jeu d'entrainement
        suby_train, suby_test = y_train.iloc[train_index], y_train.iloc[test_index]# sous echantillonnage du jeu de test
        
        catb = CatBoostRegressor(**args,random_state=42)

        catb.fit(subX_train, suby_train)
    # score_x = cross_val_score(xgb, X_train, y_train, cv= kf, scoring="neg_mean_squared_error")

        y_pred = catb.predict(subX_test)# predict for the sub test sample

        # predict in the last fold the model trained in the 9 folds 
        rmse = mean_squared_error(suby_test,y_pred,squared=False)
        mse = mean_squared_error(suby_test,y_pred)
        mae = mean_absolute_error(suby_test,y_pred)
        r2 = r2_score(suby_test, y_pred)

        ## append each metric for each fold in its corresponding table
        rmse_tab_error.append(rmse)
        mse_tab_error.append(mse)
        mae_tab_error.append(mae)
        r2_tab_error.append(r2)

    print("\n\n Hyperparameters : {}".format(args)) ## This can be commented if not needed.
    
    print("\n*********Test metrics*********\n")
    print("\t RMSE : {:.3f} \t MSE : {:.3f} \t MAE : {:.3f} \t R2 : {:.3f}".format(np.mean(np.array(rmse_tab_error)),
                        np.mean(np.array(mse_tab_error)), np.mean(np.array(mae_tab_error)), np.mean(np.array(r2_tab_error))))
   
    return np.mean(np.array(rmse_tab_error))

In [ ]:
trials_catb=hyperopt.Trials()# It'll record different values of hyperparameters tried,
#objective function values during each trial, time of trials, state of the trial (success/failure), etc

results_catb = hyperopt.fmin(objective_catb,space=search_space_catb,
                            algo=hyperopt.tpe.suggest,trials=trials_catb,max_evals = 50)

  0%|          | 0/10 [00:00<?, ?trial/s, best loss=?]0:	learn: 0.9887763	total: 1.83ms	remaining: 1.83s
1:	learn: 0.9837457	total: 4.44ms	remaining: 2.21s
2:	learn: 0.9811818	total: 6.68ms	remaining: 2.22s
3:	learn: 0.9783268	total: 8.69ms	remaining: 2.16s
4:	learn: 0.9744996	total: 13.6ms	remaining: 2.7s
5:	learn: 0.9712538	total: 15.5ms	remaining: 2.56s
6:	learn: 0.9701105	total: 17.1ms	remaining: 2.42s
7:	learn: 0.9669838	total: 18.7ms	remaining: 2.32s
8:	learn: 0.9643644	total: 20.9ms	remaining: 2.3s
9:	learn: 0.9633052	total: 24.2ms	remaining: 2.4s
10:	learn: 0.9605889	total: 25.9ms	remaining: 2.33s
11:	learn: 0.9587611	total: 28.2ms	remaining: 2.32s
12:	learn: 0.9532161	total: 29.5ms	remaining: 2.24s
13:	learn: 0.9491455	total: 30.8ms	remaining: 2.17s
14:	learn: 0.9462656	total: 32ms	remaining: 2.1s
15:	learn: 0.9445567	total: 33.3ms	remaining: 2.05s
16:	learn: 0.9411045	total: 35.9ms	remaining: 2.07s
17:	learn: 0.9393881	total: 37.9ms	remaining: 2.07s
18:	learn: 0.9369202	total

In [ ]:
results_catb

{'bagging_temperature': 25.712794204516964,
 'l2_leaf_reg': 3.8230792778891174,
 'learning_rate': 0.18410857388715868,
 'max_bin': 1531,
 'min_data_in_leaf': 26,
 'random_strength': 3.1023724168375066,
 'subsample': 0.9746975802384247}

In [ ]:
trials_catb.average_best_error()

0.22345011704530887